In [4]:
from fishsense_api_sdk.client import Client
from label_studio_sdk.client import LabelStudio
from pathlib import Path
from tqdm.notebook import tqdm
from tqdm.asyncio import tqdm_asyncio
from fishsense_api_sdk.models.headtail_label import HeadTailLabel
from fishsense_data_processing_workflow_worker.config import settings

In [2]:
PROJECT_ID = 71

In [3]:
label_studio_api_key = Path("..") / ".label_studio_api_key"

label_studio_api_key.exists()

True

In [5]:
ls = LabelStudio(base_url=f"https://labeler.e4e.ucsd.edu", api_key=label_studio_api_key.read_text().strip())

In [6]:
async with Client(settings.fishsense_api.url, settings.fishsense_api.username, settings.fishsense_api.password) as client:
    dives = await client.dives.get_canonical()

len(dives), dives

(272,
 [Dive(id=1, name='080123_FSL-01 Photos', path='2023-09-07 REEF Data Dump/080123_FSL-01 Photos', dive_datetime=datetime.datetime(2023, 8, 1, 12, 46, 27, tzinfo=TzInfo(0)), priority=<Priority.LOW: 'LOW'>, flip_dive_slate=True, camera_id=1, dive_slate_id=1),
  Dive(id=5, name='Hogfish01_MolHITW_0926_080323', path='2023.08.03.FishSense.FSL-01D/Hogfish01_MolHITW_0926_080323', dive_datetime=datetime.datetime(2023, 8, 3, 9, 27, 23, tzinfo=TzInfo(0)), priority=<Priority.LOW: 'LOW'>, flip_dive_slate=None, camera_id=1, dive_slate_id=None),
  Dive(id=8, name='DogSnapper01_MolPeLe_1024_080323', path='2023.08.03.FishSense.FSL-01D/DogSnapper01_MolPeLe_1024_080323', dive_datetime=datetime.datetime(2023, 8, 3, 10, 24, 59, tzinfo=TzInfo(0)), priority=<Priority.LOW: 'LOW'>, flip_dive_slate=None, camera_id=1, dive_slate_id=None),
  Dive(id=14, name='Hogfish01_ConchLed_1419_080323', path='2023.08.03.FishSense.FSL-01D/Hogfish01_ConchLed_1419_080323', dive_datetime=datetime.datetime(2023, 8, 3, 14, 1

In [7]:
high_priority_dives = [dive for dive in dives if dive.priority == "HIGH"]

len(high_priority_dives), high_priority_dives

(8,
 [Dive(id=279, name='111323_Alligator DeepEast Drift2_FSL05', path='drive-download-20240307T1050Z/112023_Alligator/111323_Alligator/111323_Alligator_FSL05/111323_Alligator DeepEast Drift2_FSL05', dive_datetime=datetime.datetime(2023, 11, 13, 12, 34, 8, tzinfo=TzInfo(0)), priority=<Priority.HIGH: 'HIGH'>, flip_dive_slate=None, camera_id=5, dive_slate_id=7),
  Dive(id=341, name='031424_Alligator0_FSL01', path='2024.06.20.REEF/03_2024_Alligator/031424_Alligator_FSL01/031424_Alligator0_FSL01', dive_datetime=datetime.datetime(2024, 3, 13, 23, 59, 45, tzinfo=TzInfo(0)), priority=<Priority.HIGH: 'HIGH'>, flip_dive_slate=None, camera_id=1, dive_slate_id=8),
  Dive(id=347, name='031424_Alligator0_FSL02', path='2025-02-10 REEF Data Dump SMILE 6/031424_Alligator_FSL02/031424_Alligator0_FSL02', dive_datetime=datetime.datetime(2024, 3, 14, 12, 15, 46, tzinfo=TzInfo(0)), priority=<Priority.HIGH: 'HIGH'>, flip_dive_slate=None, camera_id=2, dive_slate_id=11),
  Dive(id=349, name='031424_Alligator0

In [8]:
async with Client(settings.fishsense_api.url, settings.fishsense_api.username, settings.fishsense_api.password) as client:
    existing_headtail_labels = await tqdm_asyncio.gather(*[client.labels.get_headtail_labels(dive.id) for dive in high_priority_dives])
    existing_headtail_labels = [label for sublist in existing_headtail_labels for label in sublist]


len(existing_headtail_labels), existing_headtail_labels

100%|██████████| 8/8 [00:01<00:00,  7.81it/s]


(663,
 [HeadTailLabel(id=23477, label_studio_task_id=180912, label_studio_project_id=45, head_x=None, head_y=None, tail_x=None, tail_y=None, updated_at=datetime.datetime(2025, 9, 14, 22, 39, 3, 909745, tzinfo=TzInfo(0)), superseded=False, completed=True, label_studio_json={'annotations': [{'id': 115968, 'result': [], 'created_username': ' jessarmacsot@gmail.com, 46', 'created_ago': '2\xa0months, 1\xa0week', 'completed_by': 46, 'was_cancelled': False, 'ground_truth': False, 'created_at': '2025-09-14T22:39:03.788714Z', 'updated_at': '2025-09-14T22:39:03.788727Z', 'draft_created_at': None, 'lead_time': 10.471, 'import_id': None, 'last_action': None, 'bulk_created': False, 'task': 180912, 'project': 45, 'updated_by': 46, 'parent_prediction': None, 'parent_annotation': None, 'last_created_by': None}], 'annotations_ids': '115968', 'annotations_results': '[]', 'annotators': [46], 'avg_lead_time': 10.471, 'cancelled_annotations': 0, 'comment_authors': [], 'comment_count': 0, 'completed_at': '2

In [9]:
headtail_labels_by_image_id = {label.image_id: label for label in existing_headtail_labels}

len(headtail_labels_by_image_id), headtail_labels_by_image_id

(641,
 {78726: HeadTailLabel(id=23477, label_studio_task_id=180912, label_studio_project_id=45, head_x=None, head_y=None, tail_x=None, tail_y=None, updated_at=datetime.datetime(2025, 9, 14, 22, 39, 3, 909745, tzinfo=TzInfo(0)), superseded=False, completed=True, label_studio_json={'annotations': [{'id': 115968, 'result': [], 'created_username': ' jessarmacsot@gmail.com, 46', 'created_ago': '2\xa0months, 1\xa0week', 'completed_by': 46, 'was_cancelled': False, 'ground_truth': False, 'created_at': '2025-09-14T22:39:03.788714Z', 'updated_at': '2025-09-14T22:39:03.788727Z', 'draft_created_at': None, 'lead_time': 10.471, 'import_id': None, 'last_action': None, 'bulk_created': False, 'task': 180912, 'project': 45, 'updated_by': 46, 'parent_prediction': None, 'parent_annotation': None, 'last_created_by': None}], 'annotations_ids': '115968', 'annotations_results': '[]', 'annotators': [46], 'avg_lead_time': 10.471, 'cancelled_annotations': 0, 'comment_authors': [], 'comment_count': 0, 'completed_

In [10]:
async with Client(settings.fishsense_api.url, settings.fishsense_api.username, settings.fishsense_api.password) as client:
    species_labels = await tqdm_asyncio.gather(*[client.labels.get_species_labels(dive.id) for dive in high_priority_dives])
    species_labels = [label for sublist in species_labels for label in sublist]

len(species_labels), species_labels

100%|██████████| 8/8 [00:01<00:00,  4.66it/s]


(1218,
 [SpeciesLabel(id=1024, label_studio_task_id=222252, label_studio_project_id=57, image_url='https://orchestrator.fishsense.e4e.ucsd.edu/api/v1/data/groups_jpeg/7252dfb0db0b855616e45607f58c1c93', updated_at=datetime.datetime(2025, 10, 20, 20, 42, 14, 832143, tzinfo=TzInfo(0)), completed=True, grouping=None, top_three_photos_of_group=None, slate_upside_down=True, laser_x=1970.159985665477, laser_y=1340.3491294496944, laser_label='Red Laser', content_of_image='Slate, Laser not on slate', fish_measurable_category=None, fish_angle_category=None, fish_curved_category=None, label_studio_json={'annotations': [{'id': 117942, 'result': [{'id': 'result1', 'type': 'keypointlabels', 'value': {'x': 49.08221189998697, 'y': 44.44128413294742, 'width': 0.2, 'keypointlabels': ['Red Laser']}, 'origin': 'prediction-changed', 'to_name': 'image', 'from_name': 'laser', 'image_rotation': 0, 'original_width': 4014, 'original_height': 3016}, {'id': 'm4K68yydiZ', 'type': 'taxonomy', 'value': {'taxonomy': 

In [11]:
species_label_included = [label for label in species_labels if label.top_three_photos_of_group]

len(species_label_included), species_label_included

(258,
 [SpeciesLabel(id=1059, label_studio_task_id=222287, label_studio_project_id=57, image_url='https://orchestrator.fishsense.e4e.ucsd.edu/api/v1/data/groups_jpeg/106483baa424c4188740a4e1d69a2a21', updated_at=datetime.datetime(2025, 10, 21, 2, 1, 48, 534195, tzinfo=TzInfo(0)), completed=True, grouping=None, top_three_photos_of_group=True, slate_upside_down=None, laser_x=1907.6469079373464, laser_y=1106.1592435397524, laser_label='Red Laser', content_of_image='Fish, Hogfish (Lachnolaimus maximus)', fish_measurable_category='yes, center of fish', fish_angle_category='x < 5°', fish_curved_category='No Curve', label_studio_json={'annotations': [{'id': 118339, 'result': [{'id': 'result1', 'type': 'keypointlabels', 'value': {'x': 47.524835773227366, 'y': 36.6763674913711, 'width': 0.2, 'keypointlabels': ['Red Laser']}, 'origin': 'prediction', 'to_name': 'image', 'from_name': 'laser', 'image_rotation': 0, 'original_width': 4014, 'original_height': 3016}, {'id': 'ciK0QA_3rc', 'type': 'taxon

In [12]:
incomplete_species_labels = [label for label in species_label_included if headtail_labels_by_image_id.get(label.image_id) is None or not headtail_labels_by_image_id[label.image_id].completed]

len(incomplete_species_labels), incomplete_species_labels

(17,
 [SpeciesLabel(id=1189, label_studio_task_id=224628, label_studio_project_id=70, image_url='https://orchestrator.fishsense.e4e.ucsd.edu/api/v1/data/groups_jpeg/3aa5be29b05c9024004534b3ff434578', updated_at=datetime.datetime(2025, 12, 9, 1, 4, 7, 371746, tzinfo=TzInfo(0)), completed=True, grouping=None, top_three_photos_of_group=True, slate_upside_down=None, laser_x=2042.1125509907808, laser_y=1347.937713166261, laser_label='Red Laser', content_of_image='Fish, Nassau Grouper (Epinephelus striatus)', fish_measurable_category='yes, center of fish', fish_angle_category='x < 5°', fish_curved_category='No Curve', label_studio_json={'annotations': [{'id': 134876, 'result': [{'id': 'Q4O1MeQKd3', 'type': 'keypointlabels', 'value': {'x': 50.874752142271575, 'y': 44.69289499888133, 'width': 0.2762390456930156, 'keypointlabels': ['Red Laser']}, 'origin': 'manual', 'to_name': 'image', 'from_name': 'laser', 'image_rotation': 0, 'original_width': 4014, 'original_height': 3016}, {'id': '2efPO_PKM

In [13]:
async with Client(settings.fishsense_api.url, settings.fishsense_api.username, settings.fishsense_api.password) as client:
    incomplete_images = await tqdm_asyncio.gather(*[client.images.get(image_id=label.image_id) for label in incomplete_species_labels])

len(incomplete_images), incomplete_images

100%|██████████| 17/17 [00:00<00:00, 45.60it/s]


(17,
 [Image(id=111914, path='2025-02-10 REEF Data Dump SMILE 6/CubaTrip2024_FSL03/062624_FiveSeas_FSL03/P6260565.ORF', taken_datetime=datetime.datetime(2024, 6, 26, 6, 54, 46, tzinfo=TzInfo(0)), checksum='3aa5be29b05c9024004534b3ff434578', is_canonical=True, dive_id=383, camera_id=3),
  Image(id=111915, path='2025-02-10 REEF Data Dump SMILE 6/CubaTrip2024_FSL03/062624_FiveSeas_FSL03/P6260566.ORF', taken_datetime=datetime.datetime(2024, 6, 26, 6, 54, 58, tzinfo=TzInfo(0)), checksum='85b0fe147446a43d3ced1bcd1811c06c', is_canonical=True, dive_id=383, camera_id=3),
  Image(id=111916, path='2025-02-10 REEF Data Dump SMILE 6/CubaTrip2024_FSL03/062624_FiveSeas_FSL03/P6260567.ORF', taken_datetime=datetime.datetime(2024, 6, 26, 7, 1, 5, tzinfo=TzInfo(0)), checksum='f0c6144c00162516f6fa5df67e4abf85', is_canonical=True, dive_id=383, camera_id=3),
  Image(id=111917, path='2025-02-10 REEF Data Dump SMILE 6/CubaTrip2024_FSL03/062624_FiveSeas_FSL03/P6260568.ORF', taken_datetime=datetime.datetime(202

In [14]:
image_by_id = {image.id: image for image in incomplete_images}

len(image_by_id), image_by_id

(17,
 {111914: Image(id=111914, path='2025-02-10 REEF Data Dump SMILE 6/CubaTrip2024_FSL03/062624_FiveSeas_FSL03/P6260565.ORF', taken_datetime=datetime.datetime(2024, 6, 26, 6, 54, 46, tzinfo=TzInfo(0)), checksum='3aa5be29b05c9024004534b3ff434578', is_canonical=True, dive_id=383, camera_id=3),
  111915: Image(id=111915, path='2025-02-10 REEF Data Dump SMILE 6/CubaTrip2024_FSL03/062624_FiveSeas_FSL03/P6260566.ORF', taken_datetime=datetime.datetime(2024, 6, 26, 6, 54, 58, tzinfo=TzInfo(0)), checksum='85b0fe147446a43d3ced1bcd1811c06c', is_canonical=True, dive_id=383, camera_id=3),
  111916: Image(id=111916, path='2025-02-10 REEF Data Dump SMILE 6/CubaTrip2024_FSL03/062624_FiveSeas_FSL03/P6260567.ORF', taken_datetime=datetime.datetime(2024, 6, 26, 7, 1, 5, tzinfo=TzInfo(0)), checksum='f0c6144c00162516f6fa5df67e4abf85', is_canonical=True, dive_id=383, camera_id=3),
  111917: Image(id=111917, path='2025-02-10 REEF Data Dump SMILE 6/CubaTrip2024_FSL03/062624_FiveSeas_FSL03/P6260568.ORF', take

In [15]:
tasks = []

for label in tqdm(incomplete_species_labels):
    image = image_by_id[label.image_id]

    tasks.append({
        "data": {
            "image": f"https://orchestrator.fishsense.e4e.ucsd.edu/api/v1/data/headtail_jpeg/{image.checksum}"
        },
        "predictions": [],
        "annotations": []
    })

len(tasks), tasks

  0%|          | 0/17 [00:00<?, ?it/s]

(17,
 [{'data': {'image': 'https://orchestrator.fishsense.e4e.ucsd.edu/api/v1/data/headtail_jpeg/3aa5be29b05c9024004534b3ff434578'},
   'predictions': [],
   'annotations': []},
  {'data': {'image': 'https://orchestrator.fishsense.e4e.ucsd.edu/api/v1/data/headtail_jpeg/85b0fe147446a43d3ced1bcd1811c06c'},
   'predictions': [],
   'annotations': []},
  {'data': {'image': 'https://orchestrator.fishsense.e4e.ucsd.edu/api/v1/data/headtail_jpeg/f0c6144c00162516f6fa5df67e4abf85'},
   'predictions': [],
   'annotations': []},
  {'data': {'image': 'https://orchestrator.fishsense.e4e.ucsd.edu/api/v1/data/headtail_jpeg/7fe45079d54aff6b015969d656ce11a4'},
   'predictions': [],
   'annotations': []},
  {'data': {'image': 'https://orchestrator.fishsense.e4e.ucsd.edu/api/v1/data/headtail_jpeg/64178efbba062429fcf557422f38b67f'},
   'predictions': [],
   'annotations': []},
  {'data': {'image': 'https://orchestrator.fishsense.e4e.ucsd.edu/api/v1/data/headtail_jpeg/da2a839ebea97e060e0c6b235d2d6704'},
  

In [16]:
imported_tasks = ls.projects.import_tasks(PROJECT_ID, request=tasks, return_task_ids=True)

imported_tasks

ImportTasksProjectsResponse(annotation_count=0, could_be_tasks_list=False, data_columns=[], duration=0.15089106559753418, file_upload_ids=[], found_formats=[], predictions_count=None, task_count=17, prediction_count=0, task_ids=[224663, 224664, 224665, 224666, 224667, 224668, 224669, 224670, 224671, 224672, 224673, 224674, 224675, 224676, 224677, 224678, 224679])

In [17]:
headtail_labels = [HeadTailLabel(id=None, image_id=image.id, label_studio_task_id=task_id, label_studio_project_id=PROJECT_ID, image_url=f"https://orchestrator.fishsense.e4e.ucsd.edu/api/v1/data/groups_jpeg/{image.checksum}", updated_at=None, completed=False, label_studio_json={}, user_id=None, head_x=None, head_y=None, tail_x=None, tail_y=None, superseded=False) for task_id, image in zip(imported_tasks.task_ids, incomplete_images)]

len(headtail_labels), headtail_labels[0]

(17,
 HeadTailLabel(id=None, label_studio_task_id=224663, label_studio_project_id=71, head_x=None, head_y=None, tail_x=None, tail_y=None, updated_at=None, superseded=False, completed=False, label_studio_json={}, image_id=111914, user_id=None))

In [18]:
async with Client(settings.fishsense_api.url, settings.fishsense_api.username, settings.fishsense_api.password) as fs:
    for headtail_label in tqdm(headtail_labels):
        await fs.labels.put_headtail_label(headtail_label.image_id, headtail_label)

  0%|          | 0/17 [00:00<?, ?it/s]

In [19]:
incomplete_headtail_labels = [label for label in existing_headtail_labels if not label.completed]

len(incomplete_headtail_labels), incomplete_headtail_labels

(0, [])

In [ ]:
async with Client(settings.fishsense_api.url, settings.fishsense_api.username, settings.fishsense_api.password) as fs:
    for headtail_label in tqdm(incomplete_headtail_labels):
        headtail_label.superseded = True

        await fs.labels.put_headtail_label(headtail_label.image_id, headtail_label)

  0%|          | 0/17 [00:00<?, ?it/s]

HTTPStatusError: Server error '500 Internal Server Error' for url 'https://orchestrator.fishsense.e4e.ucsd.edu/api/v1/labels/headtail/111914'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/500